I found the instructions in the paper, https://academic.oup.com/jncics/article/2/1/pky002/4942295, and this repository to be unclear and incomplete. The intent of this notebook is to clarify that, for myself and others.

This section is a highly modified version of what is in `README_mutation_processing_commands` run with bash and linux, or tecnically my Mac.

Paper's Mutation Data Source, Reformatting, and Filtering

The file “CosmicCLP_MutantExport.tsv,” version 81, was downloaded on July 17, 2017, from the COSMIC cell line project (CLP) online database using the Sanger Institute SSH file transfer protocol (http://cancer.sanger.ac.uk/cell_lines). The mutation data of 1020 cell lines were formatted and filtered as described in the following sections. The code for these operations is available from GitHub (https://github.com/mcjarvis/Mutation-Signatures-Including-APOBEC-in-Cancer-Cell-Lines-JNCI-CS-Supplementary-Scripts). To further facilitate the reproducibility of our analyses, the mutation data from three cell lines are used as examples in this section (BC-3, BT-474, and NALM-6), and all key raw and processed numbers are provided in Supplementary Tables 1–3 (available online).

First off, you will need a copy of `CosmicCLP_MutantExport.tsv`
For the most recent version, currently v91, https://cancer.sanger.ac.uk/cell_lines/download
* Complete mutation data
* Download whole file

For some older versions, select Scripted Download and follow the instructions. Its a bit of a pain. The paper used v81. The columns have changed so you will need to take that into consideration. Unzipped, this file is just under 3GB. In addition, it is protected so I will not be including it in this repository.

This notebook will use v91.

In [1]:
date

Thu Jun  4 15:58:49 PDT 2020


In [2]:
head -1 CosmicCLP_MutantExport.v91.tsv

Gene name	Accession Number	Gene CDS length	HGNC ID	Sample name	ID_sample	ID_tumour	Primary site	Site subtype 1	Site subtype 2	Site subtype 3	Primary histology	Histology subtype 1	Histology subtype 2	Histology subtype 3	Genome-wide screen	GENOMIC_MUTATION_ID	LEGACY_MUTATION_ID	MUTATION_ID	Mutation CDS	Mutation AA	Mutation Description	Mutation zygosity	LOH	GRCh	Mutation genome position	strand	SNP	FATHMM prediction	FATHMM score	Mutation somatic status	Mutation verification status	Pubmed_PMID	ID_STUDY	Institute	Institute Address	Catalogue Number	Sample source	Tumour origin	Age	HGVSP	HGVSC	HGVSG


In [3]:
head -1 CosmicCLP_MutantExport.v91.tsv | awk -F"\t" '{print NF}'

43


In [4]:
wc -l CosmicCLP_MutantExport.v91.tsv

6055014 CosmicCLP_MutantExport.v91.tsv


**Paper's Step 1:** Download, organize, and filter raw mutation data: The fields cell line name (column 5), mutation (column 18), mutation type (column 20), version of the reference genome (column 23), chromosome position of the mutation (column 24), and DNA strand (column 25) were extracted from the “CosmicCLP_MutantExport.tsv” file using the following command:

`awk ′BEGIN{FS="\t"; OFS="\t"}; 0 !∼ /^#/ {print $5, $18, $20, $23, $24, $25}′CosmicCLP_MutantExport.tsv > cosmic_mut.txt`

The paper's command is a bit incorrect.
The broken filter is unnecessary.
And the column numbers have changed since v81 so make the appropriate changes if necessary.

And I'm not sure that `cosmic_mut.txt` is actually needed in the analysis.

In [5]:
mkdir -p v91

Change 5, 18, 20, 23, 24 and 25 to 5, 20, 22, 25, 26 and 27 for v91

In [6]:
awk 'BEGIN{FS=OFS="\t"} {print $5, $20, $22, $25, $26, $27 }' \
    CosmicCLP_MutantExport.v91.tsv > v91/Step1.tsv

In [7]:
head v91/Step1.tsv
# Sample name	Mutation CDS	Mutation Description	GRCh	Mutation genome position	strand

Sample name	Mutation CDS	Mutation Description	GRCh	Mutation genome position	strand
SK-N-FI	c.-224G>A	Unknown	38	3:11017158-11017158	+
KARPAS-1106P	c.664-54G>A	Unknown	38	5:179837258-179837258	-
SNU-1040	c.400-3C>T	Unknown	38	17:15538156-15538156	-
SU-DHL-16	c.804A>G	Substitution - coding silent	38	16:30765213-30765213	+
HT-115	c.-293+16821A>C	Unknown	38	2:187431218-187431218	-
SNU-1040	c.3581C>T	Substitution - Missense	38	6:167948300-167948300	+
NCI-H520	c.74-1475G>A	Unknown	38	1:201369702-201369702	-
T-24	c.158-22C>G	Unknown	38	3:184365111-184365111	+
GOTO	c.1677+67G>T	Unknown	38	2:134413082-134413082	+


**Paper's Step 2:** Removal of all non-single-base substitution mutations: All mutations that are not single-base substitutions (eg, insertions, deletions, and complex multibase substitutions) were filtered out of the table, leaving single-base substitution mutations annotated as nonsense, missense, or coding silent substitutions. This essential filtering step reduced the number of mutations in BT-474, BC-3, and NALM-6 from 1595 to 1407, 1537 to 1371, and 3291 to 2962, respectively.

In [8]:
head v91/Step1.tsv | awk '(NR==1 || $3 ~ /Substitution/)'

Sample name	Mutation CDS	Mutation Description	GRCh	Mutation genome position	strand
SU-DHL-16	c.804A>G	Substitution - coding silent	38	16:30765213-30765213	+
SNU-1040	c.3581C>T	Substitution - Missense	38	6:167948300-167948300	+


In [9]:
cat v91/Step1.tsv | awk 'BEGIN{FS=OFS="\t"}($3 ~ /Substitution/){print $3}' \
| sort | uniq -c

1340483 Substitution - Missense
  77549 Substitution - Nonsense
 677871 Substitution - coding silent


In [10]:
awk -F"\t" '(NR==1 || $3 ~ /Substitution/) && ($5 != "")' v91/Step1.tsv > v91/Step2.tsv

In [11]:
head v91/Step2.tsv

Sample name	Mutation CDS	Mutation Description	GRCh	Mutation genome position	strand
SU-DHL-16	c.804A>G	Substitution - coding silent	38	16:30765213-30765213	+
SNU-1040	c.3581C>T	Substitution - Missense	38	6:167948300-167948300	+
23132-87	c.1561G>A	Substitution - Missense	38	2:36808751-36808751	+
NCI-H1734	c.1591G>T	Substitution - Missense	38	13:51961859-51961859	-
HCC1428	c.86G>A	Substitution - Missense	38	2:26575951-26575951	+
OS-RC-2	c.1139C>T	Substitution - Missense	38	1:206648397-206648397	+
MZ7-mel	c.1569C>T	Substitution - coding silent	38	12:103942721-103942721	+
MCC13	c.5382C>T	Substitution - coding silent	38	12:124340400-124340400	-
MZ7-mel	c.63534G>A	Substitution - Nonsense	38	2:178552747-178552747	-


In [12]:
cat v91/Step1.tsv | awk -F"\t" '{print $1}' \
| sort | uniq -c | awk '( $2 ~ /^(BT-474|BC-3|NALM-6)$/ )'

   8668 BC-3
   9247 BT-474
  15616 NALM-6


Expecting ... above

* 1537 BC-3
* 1595 BT-474
* 3291 NALM-6

Only one of the initial counts are only off by 1.

These numbers are MUCH bigger in v91 as compared to v81!

Expecting ... below

* 1371 BC-3
* 1407 BT-474
* 2962 NALM-6
  

In [13]:
cat v91/Step2.tsv | awk -F"\t" '{print $1}' \
| sort | uniq -c | awk '( $2 ~ /^(BT-474|BC-3|NALM-6)$/ )'

   2820 BC-3
   3350 BT-474
   6607 NALM-6


**Paper's Step 3:** Additional filtering to remove nonunique chromosomal positions and file reformatting: All nonunique chromosome positions were filtered out of each cell line individually, which ensures that each mutation has only one associated chromosomal position within a cell line. A tab-separated file was created with chromosome number (eg, “chr1”), chromosomal position, reference allele, alternate (mutant) allele, strand of the substitution, and sample (cell line name) as columns. This table was reordered as follows for subsequent analyses: chr1-chr9, chrX, chrY, chr10-chr22, then by ascending chromosomal position, and it was then saved as a text file. This step reduced mutation numbers in BT-474, BC-3, and NALM-6 from 1407 to 1021, 1371 to 963, and 2962 to 2110, respectively.

In [14]:
awk 'BEGIN{FS=OFS="\t"}(NR>1){ \
split($5,a,":"); chr=a[1]; split(a[2],p,"-"); pos=p[1]; \
mut=substr($2,length($2)-2); split(mut,m,">");\
print chr, pos, m[1], m[2], $6, $1; \
}' v91/Step2.tsv | sort -n | uniq > v91/Step3.tsv

In [15]:
head v91/Step3.tsv

1	100007061	A	G	+	NCI-H1770
1	100007118	T	C	+	HCC1569
1	100007152	T	C	+	SNU-1040
1	100015410	T	C	+	HCT-116
1	100017687	T	C	+	MFE-319
1	100017693	C	T	+	CESS
1	100017782	C	T	+	MCC13
1	100049914	A	T	+	NCI-H1793
1	100049927	C	T	+	SK-MEL-2
1	100059983	C	T	+	COLO-792


In [16]:
tail v91/Step3.tsv

24	7043045	A	G	+	SNU-1040
24	7064046	G	A	+	H4
24	7064063	T	G	+	NCI-H250
24	7064065	A	T	+	NCI-H747
24	7064130	G	C	+	NCI-H747
24	7070228	G	A	+	Mo-T
24	7071601	C	T	+	EW-16
24	7085914	T	A	+	MC-CAR
24	7090169	C	T	+	KARPAS-45
24	7090185	G	C	+	LXF-289


In [17]:
cat v91/Step3.tsv | awk '( $6 ~ /^(BT-474|BC-3|NALM-6)$/ ){print $6}' | sort | uniq -c 

   1078 BC-3
   1249 BT-474
   2504 NALM-6


Expecting ... above

* 963 BC-3
* 1021 BT-474
* 2110 NALM-6

Spot on. Still gotta re-order, the purpose of which I don't understand.

## DO I REALLY NEED TO REORDER HERE?

In [18]:
wc -l v91/Step3.tsv

798992 v91/Step3.tsv


**Paper's Step 4:** Filter out “nonmutations” and “nonmatching mutations”: The hg38 reference genome (FastA file, GCA_000001405.2) was used to filter out nonmutations and nonmatching mutations (downloaded from http://hgdownload.soe.ucsc.edu/goldenPath/hg38/bigZips/ on July 16, 2017). Nonmutations are instances in which the alternate (mutant) allele matches the reference genome at that position. Nonmatching mutations are instances in which the reference allele does not match the reference genome at that position. These anomalies were filtered out of the single-base substitution mutation data set. This step caused a modest reduction in mutation numbers in a small number of cell lines. For instance, the numbers above for BT-474 and BC-3 were unchanged, but the number for NALM-6 reduced from 2110 to 2108. These single-base substation numbers were used to plot medians in Figure 1, and raw values are listed for each trinucleotide context in Supplementary Table 1 (available online). Following the filtering steps described above, the total single-base substitution mutation count across all cell lines was 663 075.

In [19]:
head v91/Step3.tsv

1	100007061	A	G	+	NCI-H1770
1	100007118	T	C	+	HCC1569
1	100007152	T	C	+	SNU-1040
1	100015410	T	C	+	HCT-116
1	100017687	T	C	+	MFE-319
1	100017693	C	T	+	CESS
1	100017782	C	T	+	MCC13
1	100049914	A	T	+	NCI-H1793
1	100049927	C	T	+	SK-MEL-2
1	100059983	C	T	+	COLO-792


In [20]:
mkdir -p v91/Step4a

In [21]:
date

Thu Jun  4 16:01:36 PDT 2020


Should I be converting to complement for reverse (-) strand? Or was this a bad idea?

I downloaded hg38.fa.gz. I gunzipped it, removed the "chr" prefix, bgzipped and finally indexed it.
```
zcat hg38.fa.gz | sed 's/^>chr/>/' > hg38_num.fa
samtools faidx hg38_num.fa
```

This next step will take quite a while, about 3 hours, with all of the reference checks.

In [22]:
awk 'BEGIN{FS=OFS="\t";
    comp["A"]="T"
    comp["T"]="A"
    comp["C"]="G"
    comp["G"]="C"
    comp["N"]="N"
}{
    chr=$1; pos=$2; ref=$3; alt=$4; strand=$5; sample=$6
    if(chr==23) chr="X"
    if(chr==24) chr="Y"
    #cmd="samtools faidx hg38.fa chr"chr":"pos"-"pos" | tail -1 "
    cmd="samtools faidx hg38_num.fa "chr":"pos"-"pos" | tail -1 "
    cmd|getline ref38
    close(cmd)
    ref38=toupper(ref38)
    ref=toupper(ref)
    alt=toupper(alt)
    if(strand == "-"){ ref=comp[ref]; alt=comp[alt] }
    if( ref == ref38 ) {
        if( alt == ref38 ){
#Nonmutations are instances in which the alternate (mutant)
#allele matches the reference genome at that position.
            print "Nonmutation?", chr, pos, ref38, ref, alt, strand, sample >> "v91/Step4a-nonmutation.tsv"
            close("v91/Step4a-nonmutation.tsv")
        }else{
            filename=$6
            gsub("/","_",filename)
            filename="v91/Step4a/"filename".tsv"
            print chr, pos, ref, alt, strand, sample >> filename
            close(filename)
        }
    }else{
#Nonmatching mutations are instances in which the reference 
#allele does not match the reference genome at that position.
        print "Nonmatching mutation?", chr, pos, ref38, ref, alt, strand, sample >> "v91/Step4a-nonmatching.tsv"
        close("v91/Step4a-nonmatching.tsv")
    }
}' v91/Step3.tsv

In [23]:
date

Thu Jun  4 19:16:07 PDT 2020


In [24]:
wc -l v91/Step3.tsv

798992 v91/Step3.tsv


Expecting Step4 to be only 663075 but won't be.

In [25]:
cat v91/Step4a/*.tsv | wc -l

798981


In [26]:
wc -l v91/Step4a-nonmatching.tsv

11 v91/Step4a-nonmatching.tsv


In [27]:
# wc -l v91/Step4a-nonmutation.tsv

wc: Step4a-nonmutation.tsv: No such file or directory

In [28]:
mkdir -p v91/Step4b

In [29]:
#for f in *-Step4a.tsv ; do n=${f/Step4a/Step4b}; sort -n $f > $n ;  done
for f in v91/Step4a/*tsv; do
    b=$( basename $f ) 
    sort -n $f > v91/Step4b/$b
done

In [30]:
cat v91/Step4b/*.tsv | wc -l

798981


Combine and remove "strand" column

In [31]:
cat v91/Step4b/*.tsv | awk 'BEGIN{FS=OFS="\t"}{print $1,$2,$3,$4,$6}' > v91/cosmic_mut.txt

May need to install some perl modules

`cpan install -T XML::DOM::XPath BioPerl Bio::DB::Fasta`

Also, chromosome naming convention must match so you may need to add "chr" prefix to dataset here or in count_trinuc_muts_v8.pl script. The hg38 reference includes the "chr" prefix. hg38_num does not.

In [40]:
head v91/cosmic_mut.txt

X	124385814	G	A	201T
X	13760512	C	G	201T
X	141697643	G	C	201T
X	153346872	G	T	201T
X	15347338	G	C	201T
X	21856496	C	T	201T
X	45164212	C	A	201T
X	55146153	G	T	201T
X	8466103	T	C	201T
1	101240008	C	A	201T


In [41]:
#for f in Step4b/*.tsv; do
#    ./count_trinuc_muts_v8.pl pvcf hg38.fa $f > $f.count.txt
#done

In [42]:
#rename 's/tsv.\d*.count/count/' *-Step4b.tsv.*.count.txt
#rename 's/tsv.\d*.count/count/' Step4b/*.tsv.*.count.txt

In [43]:
#head -1 $( ls Step4b/*count.txt | head -1 ) > cosmic_mut_all_sort.txt
#tail -n +2 -q Step4b/*count.txt >> cosmic_mut_all_sort.txt

In [44]:
cat v91/Step4b/*.tsv > v91/Step4b.tsv

In [45]:
wc -l v91/Step4b.tsv

798981 v91/Step4b.tsv


In [46]:
#awk 'BEGIN{FS=OFS="\t"}{print "chr"$1,$2,$3,$4,$5,$6}' v91/Step4b.tsv > v91/Step4c.tsv
awk 'BEGIN{FS=OFS="\t"}{print $1,$2,$3,$4,$5,$6}' v91/Step4b.tsv > v91/Step4c.tsv

In [47]:
head v91/Step4c.tsv

X	124385814	G	A	-	201T
X	13760512	C	G	+	201T
X	141697643	G	C	-	201T
X	153346872	G	T	+	201T
X	15347338	G	C	-	201T
X	21856496	C	T	+	201T
X	45164212	C	A	-	201T
X	55146153	G	T	-	201T
X	8466103	T	C	+	201T
1	101240008	C	A	+	201T


In [48]:
#./count_trinuc_muts_v8.pl pvcf hg38.fa v91/Step4c.tsv > v91/cosmic_mut_all_sort.txt
./count_trinuc_muts_v8.pl pvcf hg38_num.fa v91/Step4c.tsv > v91/cosmic_mut_all_sort.txt

creating fasta db... complete!
Exists (rc)GCCTACTCCCCTGAGGACAATTCCACACAGTGGTTTCACAA in repeat hash. Skipping.
Exists (rc)GAGCAACCGCCTTTATTCACGGTAAACATATTTTCTTTAAT in repeat hash. Skipping.
Exists ACCCTGCGACGAGCAAAAAGG in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists CCCAGCACCTGTGGTGGGAAT in repeat hash. Skipping.
Exists GTGGAGTGCCCGCCTGCTCAC in repeat hash. Skipping.
Exists ATCAATCGCATGAAGGCTGAT in repeat hash. Skipping.
Exists ACAGGACTCACAAGGCCAGGT in repeat hash. Skipping.
Exists (rc)CGGGTCCTGGGCCAGGCCAAGCAGGAGGTGGAACATAAGAA in repeat hash. Skipping.
Exists TACAAGGAACGATTAAATAGA in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists ACAGGACTCACAAGGCCAGGT in repeat hash. Skipping.
Exists CCTGCGGGGTGGGCGTGAGGA in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists (rc)GCAGCGGTGAGAGCAGCTCCACCCGCCGCTCAAGTGAGGAT in repeat hash. Ski

Exists (rc)TGATTTTGGTCTAGCTACAGTGAAATCTCGATGGAGTGGGT in repeat hash. Skipping.
Exists TGGACACGATAATGTTCCTAT in repeat hash. Skipping.
Exists CAAATGTGAAGAATGTGGCAA in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists (rc)CAGAGGCAGAGAAAGGACGACAGGCAGAGAGAGGACGACAG in repeat hash. Skipping.
Exists AAACAGCCACCAACAATGCTT in repeat hash. Skipping.
Exists (rc)GCGGGGAGCCCCGCTTCATCTCAGTGGGCTACGTGGACGAC in repeat hash. Skipping.
Exists (rc)AATGCCTCCTTTGTCCGTCCGCCGGCCAAGGAGGGCTGGAG in repeat hash. Skipping.
Exists GGCAGTGGAGCCCCAAATGAG in repeat hash. Skipping.
Exists (rc)CCCACGAAGGCTGTGAAAAAGTAGTTGTTCAGAACAACCTT in repeat hash. Skipping.
Exists TGAAGAGGCCCGGGGAGGACA in repeat hash. Skipping.
Exists (rc)GCAGCTACAAGATGAGACCAACCACCTAAGGAAGGAGCTAG in repeat hash. Skipping.
Exists (rc)GAGCAAGCAGGAGCTGGAGAGGATGGCGGCCATCAGCAACA in repeat hash. Skipping.
Exists GGAGGAGAAGCGCAAGGCTGA in repeat hash. Skipping.
Exists (rc)GTTCCAGAGATGGAGCAGACTTGAAGGAGAATATAAAGAAC in repeat

Exists ACTTATGCTCAAGTCAGTTCA in repeat hash. Skipping.
Exists ACTTCTGAAGGTACCAGCATG in repeat hash. Skipping.
Exists (rc)TGATTTTGGTCTAGCTACAGTGAAATCTCGATGGAGTGGGT in repeat hash. Skipping.
Exists (rc)GTGCAAAGTGTGCCAGAACTGCAAGTAAGTTTTCATTTCAA in repeat hash. Skipping.
Exists TCCGCTGCTCGGAGGATGAGA in repeat hash. Skipping.
Exists TACCTGAGTCCCAGTGCCAGA in repeat hash. Skipping.
Exists (rc)GGCGTGGTCACGAACTGGCCGCCGTCGCTGGAGGCCGCACT in repeat hash. Skipping.
Exists TCTGTGGCCACCCCCTCCTCC in repeat hash. Skipping.
Exists AGCTACCAGCGTTACAGCCAT in repeat hash. Skipping.
Exists (rc)GGGGTGCCAAGCGGGTCTCCATCAATGGGTGTGGCAGCAGC in repeat hash. Skipping.
Exists CACATGTTAACCAGACACAGG in repeat hash. Skipping.
Exists CAAGACCATCGGCAGCACGTA in repeat hash. Skipping.
Exists (rc)CTCCAAAGTTACTAAAAAAAGTGACGATAAGAATTCAGAAA in repeat hash. Skipping.
Exists (rc)GACGAAGAGGAGGAGGAGGAAGAGGAGGAGGATGACGATGA in repeat hash. Skipping.
Exists GTGGCAAAGCCTTCATTTGGT in repeat hash. Skipping.
Exists (rc)CCGCGCTTTATCAAGATTAT

Exists AGGGGCCCTCCTCGCCAAAGA in repeat hash. Skipping.
Exists ACCGGCGCCCGGTGGCCGAGC in repeat hash. Skipping.
Exists TCTCCCTCTGCGCCGTAGCAC in repeat hash. Skipping.
Exists (rc)AAGATGATGCCTGTTCTTAGCGAGGATACAATATTACAGGT in repeat hash. Skipping.
Exists (rc)GACACAGAAGAATCCACACAGGGGAAAAACCATATGAATGC in repeat hash. Skipping.
Exists (rc)CGACGCCGCGAGTCCGAGAGAGGAGCCGCGGGCGCCGTGGA in repeat hash. Skipping.
Exists GTGGGAGAGGCTGGTCTCGGT in repeat hash. Skipping.
Exists (rc)CCCCCAGCAAGGCTGGCCCCCCCGGGACATCACTGTAACTC in repeat hash. Skipping.
Exists AGAATGTACCCGACTTGAAAA in repeat hash. Skipping.
Exists (rc)TAGAAGTAGCATCAGAAGAAGAGCAAGAAAGGGAAGGGAGT in repeat hash. Skipping.
Exists (rc)TCCCTCGGGTCAGTCAGTACCGCCTTGCTGCCCACCTGGGA in repeat hash. Skipping.
Exists TCACTGATGAACAGTTTCTGG in repeat hash. Skipping.
Exists (rc)GAAATGAGGGGCTACGCGGAGAAGGTGAGGAGCGCGGCCCT in repeat hash. Skipping.
Exists (rc)GGGGAGGCGGGCCCACCCCCAGAGAGGGAAGGCAGTGGTTC in repeat hash. Skipping.
Exists (rc)TCCCAGTTCTAGAGCGCATCCGGGATC

Exists (rc)AGCAGAGAAAAAGTCTTCCTGTTTTATCGAATGGGGACTTC in repeat hash. Skipping.
Exists (rc)ATGCCATCGTTCGGGGCGTCAGCCCCAGGCAAGTCCATCGA in repeat hash. Skipping.
Exists (rc)TGGCGGACCTTGATTCGCCTCCGAAGCTGTCAGGGGTGCAG in repeat hash. Skipping.
Exists (rc)GAGGAGTCGGTGCGGGAGGCCAGCCTCTGCAAGAAGCTGCG in repeat hash. Skipping.
Exists (rc)ACCGCCTCCGAGGACGGCACGCTCAAGCTCTGGAACCTGCA in repeat hash. Skipping.
Exists (rc)ACAAAAACGGAATGTACACATGAGAGAAAAATCTTTCCAAT in repeat hash. Skipping.
Exists CCCCAGAGAAGGCCAAGTCCC in repeat hash. Skipping.
Exists CTCGCGTATCTCATCTCCGCC in repeat hash. Skipping.
Exists CAGAGCCTCCCAAGACTCGGA in repeat hash. Skipping.
Exists (rc)CTTCCTGGCTCCAGTCACATGGCCAGATAAGGTGGTGTGTG in repeat hash. Skipping.
Exists TGAAATCACTGAGCAGGAGAA in repeat hash. Skipping.
Exists CATCCCCACTTTCCAAACTGA in repeat hash. Skipping.
Exists (rc)CCTCCGCGGGTATGACCAGTCCGCCTACGACGGCAAGGATT in repeat hash. Skipping.
Exists GCTGAAGGTACCAGCATAGCA in repeat hash. Skipping.
Exists ACTTATGCTCAAGTCAGTTCA in repeat

...

Exists (rc)CAATCAGGAGGCCGCCTGAAGAGGCCAGTCAATGTCCCCTT in repeat hash. Skipping.
Exists TTGCCCAGAAGCCATCGTGTC in repeat hash. Skipping.
Exists (rc)GGTCTCCAGAGTTGGTTTGCTCTGGGTATTATTATTAAATT in repeat hash. Skipping.
Exists (rc)GCCTGCTTTGGGGGTGCTGGAGGCTTTGGCACTGGTGGCTT in repeat hash. Skipping.
Exists CCATTGAAATGCCCCAGTATT in repeat hash. Skipping.
Exists GTCTCAAGAACCAGAAATAAA in repeat hash. Skipping.
Exists (rc)AACTGCTCGCTCTTGGTGAAAATTATGAACTGCTTATCTAT in repeat hash. Skipping.
Exists (rc)TGGCCAGGAAGTCAGGAAACTAGACCTGCCAGTGCTGTTCC in repeat hash. Skipping.
Exists CTCGGGACCCATTTGCCTGCT in repeat hash. Skipping.
Exists (rc)ATGCAACTGTTGGGTGGCATCCAATCAACCTGTTCCTCCCC in repeat hash. Skipping.
Exists (rc)AAAATAGCCCAGGAAGATCCAGAGAAGCAGAGGAAAGTAAG in repeat hash. Skipping.
Exists CCCCGACCCTGAGGCCCTCAA in repeat hash. Skipping.
Exists GCAACCAGTGCGGGAAAGCAT in repeat hash. Skipping.
Exists (rc)GTTGAGGGACCCACAGCATGATCTAGATCGAGTAAAGAAAC in repeat hash. Skipping.
Exists CCGTGCAACTGAAATGTGGAT in repeat

Exists (rc)CAAAACAAAGGCCAAAATCAATATACCTGCTGATATGGTGT in repeat hash. Skipping.
Exists (rc)CAGGGAGTACAAGAAGGAGTTTGAGAAGTGGAAGACCAAGT in repeat hash. Skipping.
Exists (rc)CATTTCAGCTACAGCAGAGAGATTCTCTGGTTATATGCAGA in repeat hash. Skipping.
Exists GAGAAGGGGCCGCCGCGGGTG in repeat hash. Skipping.
Exists TGAAGAAAAGGAATGTTTCAG in repeat hash. Skipping.
Exists ACACACCATCGGCCCAGCCCC in repeat hash. Skipping.
Exists (rc)TGCATCTATTTAGAAAATGGGATGCAGGATTCAAGGAAGAA in repeat hash. Skipping.
Exists (rc)CTCCAGACCTGATCAGAATTCGGACCTTCAGATTCGTACCG in repeat hash. Skipping.
Exists GGATGGGTCCAGTGTCACCGG in repeat hash. Skipping.
Exists (rc)CCTGAGCCCGAGCCTGAGAATGACTATGAGGACGTTGAGGA in repeat hash. Skipping.
Exists (rc)GCCTGAGCCCGAGCCTGAGAATGACTATGAGGACGTTGAGG in repeat hash. Skipping.
Exists (rc)AGCCTGAGCCCGAGCCTGAGAATGACTATGAGGACGTTGAG in repeat hash. Skipping.
Exists (rc)AGGAAGAGCCAGTGTACGAAGCAGAGCCTGAGCCTGAGCCC in repeat hash. Skipping.
Exists (rc)GAAATCCGCTAGCAAAGAAGAACTCAAGAAAGACGTTAAGA in repeat hash. 

Exists (rc)ACCGAGAGCAACTACTGTACGCAGCTGGCGCAGATCCAGGC in repeat hash. Skipping.
Exists TCTCACAGCCGCAGACACTAG in repeat hash. Skipping.
Exists ATACCTATAATTTAGGAATTG in repeat hash. Skipping.
Exists (rc)TGTGAGGCGCTGCCCCCACCATGAGCGCTGCTCAGATAGCG in repeat hash. Skipping.
Exists (rc)ATTCCGGGATTCCCAATTCTCATCAACTTTAAGGCCACCAA in repeat hash. Skipping.
Exists (rc)CCAGACATGGAGGAAGACGATGATCAGAAAGCTGTGAAAGA in repeat hash. Skipping.
Exists TACGACGAGAAGCGGGGTGCC in repeat hash. Skipping.
Exists GCCTGCTGGGGTGAGCAGGCT in repeat hash. Skipping.
Exists (rc)TGGGCCAAGGGACGCTACACAGAAGGCGCGGAGCTGACGGA in repeat hash. Skipping.
Exists (rc)GACCCAGATGAATGTGGGAGCGATTACATTAGTGAGTTCCG in repeat hash. Skipping.
Exists (rc)GCCCACCTGCTGCCCTCGCCCGAGCCCAGCCCAGAAGGCAG in repeat hash. Skipping.
Exists (rc)CATTTCTTCTAATTCTATTCGCTATCATAAAAGGACTCACA in repeat hash. Skipping.
Exists (rc)TAATTCATATGGAAGAGAAACCTTGCAAATGTGAAGAATGT in repeat hash. Skipping.
Exists (rc)CTGGAGAAAAACCCTACAAATGTGAAGAATGTGGAAAAGCT in repeat hash. 

Exists CTATAAATATCGAGAGGACTT in repeat hash. Skipping.
Exists ACTTGACCGGCTAAATGCCCC in repeat hash. Skipping.
Exists (rc)CTGTCCCCTGGCGGGCATGCAGAGGTAAGACCTGGCCAGGG in repeat hash. Skipping.
Exists GAATCCTCTAAAGCAACTCCT in repeat hash. Skipping.
Exists (rc)CAAAGCCCTCATGGATGAAATTGTGAAAGCCACTTCCAAGG in repeat hash. Skipping.
Exists GCTGAAGGTACCAGCATAGCA in repeat hash. Skipping.
Exists CCACTTATGCTCAAGTCAGTT in repeat hash. Skipping.
Exists CACTTATGCTCAAGTCAGTTC in repeat hash. Skipping.
Exists ACTTATGCTCAAGTCAGTTCA in repeat hash. Skipping.
Exists TAGATTTAATTCACCCTGTCA in repeat hash. Skipping.
Exists (rc)CTTTTACACATAAAATCAACGTGGCAGCAGAGAAGGGAGCA in repeat hash. Skipping.
Exists (rc)TGTGGTTAAGCGCTGGATCAATGAAGCCCAAGAAGCTGCAT in repeat hash. Skipping.
Exists TTCTGGCGACGAAAGCAGCTT in repeat hash. Skipping.
Exists GATGACAGACGTCCTGATGCC in repeat hash. Skipping.
Exists TCCCGAAGTCGGGGCCCAGCG in repeat hash. Skipping.
Exists GACAGATCATCGGGCGGGTGA in repeat hash. Skipping.
Exists TGTATGACAAGCTCATA

Exists CCGGCTGGGGCTGCCCATCCA in repeat hash. Skipping.
Exists GCAGCTGGCTGCGGAGGTGAA in repeat hash. Skipping.
Exists GGCTTTTCCCGCCACAAATAC in repeat hash. Skipping.
Exists (rc)GTACCACAACGGTCGTTGGCTGCAGGAGGGTCCAGCTGCCT in repeat hash. Skipping.
Exists GAGACCCCGGCCTTCCAGGCC in repeat hash. Skipping.
Exists CCTGACAAGGCGGAGCCTCCC in repeat hash. Skipping.
Exists (rc)TACAGCTTGGTGCGGGCCATCAGCGAGGCGGGCGCGCCCCC in repeat hash. Skipping.
Exists (rc)ACCTCAGCTGCGGAGAGGGATGGCAGTGGTGAGTGAGAGGC in repeat hash. Skipping.
Exists GGACCCTTCCCCGGTCAGCTC in repeat hash. Skipping.
Exists GGTCTGAATCTCCCCTGGCCA in repeat hash. Skipping.
Exists (rc)CAGTCTGCGTGTACTCAATCGCCACTTCTCCCAGGATCTTA in repeat hash. Skipping.
Exists (rc)ACCCTGATGAGGGTGTGGCCGGGGCACCCACAGGGTCTTCC in repeat hash. Skipping.
Exists TACTGCTGGGAAAACTTTGTG in repeat hash. Skipping.
Exists (rc)TACCCCCCGGACCAGGAGAGCGGGGGCGCAGCCAGGCTTGC in repeat hash. Skipping.
Exists (rc)TCGCTGCTGCTGGAACTAGCCGTCTACGGGCTTCTGGCCTA in repeat hash. Skipping.
Exists 

In [49]:
head v91/cosmic_mut_all_sort.txt

#chr	pos	5'tetranuc	3'tetranuc	trinuc	mut	trinuc_mut	strand	flank41bp	Ccount	TCcount	TCAcount	TCTcount	YTCAcount	RTCAcount	sample
X	124385814	CACC	ACCA	ACC	G>A	A[G>A]C	-	CAGAGTCTTATACAAGTACACCAAGCAAGCAAGGCTTTCTG	18	3	0	3	0	0	201T
X	13760512	TCCA	CCAG	CCA	C>G	C[C>G]A	+	GCCTTCAAAAACATTACTTCCAGTTCCCCGGAAAGACATAT	17	5	2	2	1	0	201T
X	141697643	TCCG	CCGA	CCG	G>C	C[G>C]G	-	CTCAGACCCGCAACCTGCTCCGAAAAAACTAAAAACATCTG	19	5	1	2	1	0	201T
X	153346872	AGGA	GGAG	GGA	G>T	G[G>T]A	+	GGGAAGATGCCCAGCCACAGGAGATGGCGTCCACAAGCTTC	25	6	2	2	0	0	201T
X	15347338	ACCA	CCAG	CCA	G>C	C[G>C]A	-	CCACTCTCATCTCCAGGAACCAGCTCTCTGTGGGCCACACA	24	7	1	3	1	0	201T
X	21856496	AACG	ACGA	ACG	C>T	A[C>T]G	+	CTCTCAGCCATGGCCTCCAACGAAGATTTCTCCATCACACA	21	8	4	4	1	1	201T
X	45164212	GTGT	TGTA	TGT	C>A	T[C>A]T	-	GAGAGAACTAAAGTTCCTGTGTATGCTGAGATAACACCAGT	17	6	1	2	1	0	201T
X	55146153	TCCC	CCCA	CCC	G>T	C[G>T]C	-	CCATGCCAAGGTCTTTACTCCCATATCAACCAGACCTTGAA	19	5	2	2	1	1	201T
X	8466103	ACTG	CTGA	CTG	T>C	C[T>C]G	+	GAGCCAGGTGGAGGAACCACTGAGTCAGGAGAGCGAG

`count_trinuc_muts_v8.pl` filters quite a few mutations out for some reason.

In [50]:
wc -l v91/cosmic_mut_all_sort.txt

719277 v91/cosmic_mut_all_sort.txt


The supplementary data associated with this paper pky002_supp.zip contains
* Supplementary Table 1-mutation counts.xls  
* Supplementary Table 2-COSMIC signatures.xls  
* Supplementary Table 3-APOBEC signatures.xls
  
2 of these spreadsheets include sample and tissue columns which I extracted to create the tab-separated, 2-column cosmic_tissue_type.txt file. There is no header in this file and column 1 is the Cell Line and column 2 is the Tissue of Origin.

In [51]:
head "Supplementary Table 1-mutation counts.csv"

Tissue of Origina,Cell Line,Total Number of Mutations,A[C>A]A,A[C>A]C,A[C>A]G,A[C>A]T,C[C>A]A,C[C>A]C,C[C>A]G,C[C>A]T,G[C>A]A,G[C>A]C,G[C>A]G,G[C>A]T,T[C>A]A,T[C>A]C,T[C>A]G,T[C>A]T,A[C>G]A,A[C>G]C,A[C>G]G,A[C>G]T,C[C>G]A,C[C>G]C,C[C>G]G,C[C>G]T,G[C>G]A,G[C>G]C,G[C>G]G,G[C>G]T,T[C>G]A,T[C>G]C,T[C>G]G,T[C>G]T,A[C>T]A,A[C>T]C,A[C>T]G,A[C>T]T,C[C>T]A,C[C>T]C,C[C>T]G,C[C>T]T,G[C>T]A,G[C>T]C,G[C>T]G,G[C>T]T,T[C>T]A,T[C>T]C,T[C>T]G,T[C>T]T,A[T>A]A,A[T>A]C,A[T>A]G,A[T>A]T,C[T>A]A,C[T>A]C,C[T>A]G,C[T>A]T,G[T>A]A,G[T>A]C,G[T>A]G,G[T>A]T,T[T>A]A,T[T>A]C,T[T>A]G,T[T>A]T,A[T>C]A,A[T>C]C,A[T>C]G,A[T>C]T,C[T>C]A,C[T>C]C,C[T>C]G,C[T>C]T,G[T>C]A,G[T>C]C,G[T>C]G,G[T>C]T,T[T>C]A,T[T>C]C,T[T>C]G,T[T>C]T,A[T>G]A,A[T>G]C,A[T>G]G,A[T>G]T,C[T>G]A,C[T>G]C,C[T>G]G,C[T>G]T,G[T>G]A,G[T>G]C,G[T>G]G,G[T>G]T,T[T>G]A,T[T>G]C,T[T>G]G,T[T>G]T,,,,,,,,,
Adrenal Gland,SW13,457,6,4,6,3,6,7,9,3,8,9,5,9,7,5,11,6,8,3,6,3,2,4,0,3,6,5,3,1,6,5,2,2,8,9,15,5,11,11,19,15,8,10,18,6,10,10,10,8,3,2,3,1,2,6,10,2,1,2,6,1,2,3,1,1,4,3,4,

In [52]:
awk 'BEGIN{FS=",";OFS="\t"}(NR>1){print $2,$1}' \
    "Supplementary Table 1-mutation counts.csv" > v91/cosmic_tissue_type.txt

In [53]:
head v91/cosmic_tissue_type.txt

SW13	Adrenal Gland
ACN	Autonomic Ganglia
BE2-M17	Autonomic Ganglia
CHP-126	Autonomic Ganglia
CHP-134	Autonomic Ganglia
CHP-212	Autonomic Ganglia
GI-ME-N	Autonomic Ganglia
GOTO	Autonomic Ganglia
IMR-5	Autonomic Ganglia
KELLY	Autonomic Ganglia


In [54]:
date

Thu Jun  4 20:03:25 PDT 2020


This notebook could be run outside

```
jupyter nbconvert --to notebook --execute Reproduce-1.ipynb --output Reproduce-1-out.ipynb --ExecutePreprocessor.timeout=14400
```